MIT License

Copyright (c) 2021 Taiki Miyagawa and Akinori F. Ebihara

Permission is hereby granted, free of charge, to any person obtaining a copy
of this software and associated documentation files (the "Software"), to deal
in the Software without restriction, including without limitation the rights
to use, copy, modify, merge, publish, distribute, sublicense, and/or sell
copies of the Software, and to permit persons to whom the Software is
furnished to do so, subject to the following conditions:

The above copyright notice and this permission notice shall be included in all
copies or substantial portions of the Software.

THE SOFTWARE IS PROVIDED "AS IS", WITHOUT WARRANTY OF ANY KIND, EXPRESS OR
IMPLIED, INCLUDING BUT NOT LIMITED TO THE WARRANTIES OF MERCHANTABILITY,
FITNESS FOR A PARTICULAR PURPOSE AND NONINFRINGEMENT. IN NO EVENT SHALL THE
AUTHORS OR COPYRIGHT HOLDERS BE LIABLE FOR ANY CLAIM, DAMAGES OR OTHER
LIABILITY, WHETHER IN AN ACTION OF CONTRACT, TORT OR OTHERWISE, ARISING FROM,
OUT OF OR IN CONNECTION WITH THE SOFTWARE OR THE USE OR OTHER DEALINGS IN THE
SOFTWARE.

# Extract Bottleneck Features and Save Them in a TFRecords File
### Instruction
- Change "User-defined parameters" cell below.
- RUN TWICE for each dataset to create train and test TFRs. 
- E.g.
- NMNIST-H_train.tfrecords -> feature extractor -> NMNIST-H_train_feat.tfrecords
- NMNIST-H_test.tfrecords -> feature extractor -> NMNIST-H_test_feat.tfrecords
- NMNIST-100f_train.tfrecords -> feature extractor -> NMNIST-100f_train_feat.tfrecords
- NMNIST-100f_test.tfrecords -> feature extractor -> NMNIST-100f_test_feat.tfrecords

In [1]:
# tf.__version__ = 2.0.0
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import os, time
import PIL
import matplotlib.pyplot as plt
import numpy as np
import tensorflow as tf

from datasets.data_processing import decode_nosaic_mnist, reshape_for_featext,\
    normalize_images_nosaic_mnist,\
    read_tfrecords_nosaic_mnist, decode_feat
from models.backbones_fe import ResNetModel, get_ressize_dependent_params
from models.losses import get_loss_fe

def set_gpu_devices(gpu):
    physical_devices = tf.config.experimental.list_physical_devices('GPU')
    assert len(physical_devices) > 0, "Not enough GPU hardware devices available"
    tf.config.experimental.set_visible_devices(physical_devices[gpu], 'GPU')
    tf.config.experimental.set_memory_growth(physical_devices[gpu], True)

    
def np_to_tfr_fe(x, y, writer):
    """Save a np.array to a tfrecord file. DO NOT FORGET writer.close().
    Args:
        x: data: np.ndarray, dtype=float32
        y: label: int, dtype=int64
        writer: tf.io.TFRecordWriter object. Don't forget writer.close()
    """
    def _bytes_feature(value):
        return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value]))
    def _int64_feature(value):
        return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))
    def _float_feature(value):
        return tf.train.Feature(float_list=tf.train.FloatList(value=[value]))

    # Make an Example object that has one record data
    example = tf.train.Example(features=tf.train.Features(feature={
        'video': _bytes_feature(x.tostring()),
        'label': _int64_feature(y)
        }))

    # Serialize the example object and make a TFRecord file
    writer.write(example.SerializeToString())

    
def read_tfrecords_nosaic_mnist_tmp(record_file_train, record_file_test, batch_size):
    """Reads TFRecord file and make parsed dataset tensors. Returns train, validation and test dataset tensors with 5:1:1 split.
    Args:
        record_file_train: A string. Path to training nosaic MNIST tfrecord file.
        record_file_test: A string. Path to test nosaic MNIST tfrecord file.
        batch_size: An int.
        shuffle_buffer_size: An int. Larger size leads to larger CPU memory consumption.
    Return:
        parsed_image_dataset_train: A dataset tensor.
        parsed_image_dataset_valid: A dataset tensor.
        parsed_image_dataset_test: A dataset tensor.
    Usage:
        # Training loop
        for i, feats in enumerate(parsed_image_dataset):
            video_batch = tf.io.decode_raw(feats['video'], tf.uint8)
            video_batch = tf.cast(video_batch, tf.float32)
            video_batch = tf.reshape(video_batch, (-1, 20, 28, 28, 1)) # (B, T, H, W, C)
            label_batch = tf.cast(feats["label"], tf.int32) # (B, )        
        # That is,
        for i, feats in enumerate(parsed_image_dataset):
            video_batch, label_batch = decode_nosaic_mnist(feats)
    Remark:
        drop_remainder=True for validation datasets for simplicity of code.
    """
    def _parse_image_function(example_proto):
        return tf.io.parse_single_example(example_proto, {
                    'video': tf.io.FixedLenFeature([], tf.string),
                    'label': tf.io.FixedLenFeature([],tf.int64)
                    })

    raw_image_dataset = tf.data.TFRecordDataset(record_file_train)
    raw_image_dataset_test = tf.data.TFRecordDataset(record_file_test)
    #parsed_image_dataset = raw_image_dataset.map(_parse_image_function)
    parsed_image_dataset_train = raw_image_dataset.map(_parse_image_function)
    parsed_image_dataset_test = raw_image_dataset_test.map(_parse_image_function)

    #parsed_image_dataset_train = parsed_image_dataset.take(50000)
    #parsed_image_dataset_valid = parsed_image_dataset.skip(50000)

    #parsed_image_dataset_train = parsed_image_dataset_train.shuffle(shuffle_buffer_size)

    parsed_image_dataset_train = parsed_image_dataset_train.batch(batch_size, drop_remainder=False)
    #parsed_image_dataset_valid = parsed_image_dataset_valid.batch(batch_size, drop_remainder=True) ###
    parsed_image_dataset_test = parsed_image_dataset_test.batch(batch_size, drop_remainder=False) 

    #return parsed_image_dataset_train, parsed_image_dataset_valid, parsed_image_dataset_test
    return parsed_image_dataset_train, parsed_image_dataset_test


def checkpoint_logger_tmp(model, flag_resume, root_ckptlogs,
    subproject_name, exp_phase, comment, time_stamp, path_resume=None, 
    max_to_keep=3, config_path=None):
    """Make ckpt and manager objects, and restore the latest checkpoint if necessary.
    Args:
        model: A tf.keras.Model object.
        flag_resume: A boolean. Whether to resume training from the latest ckpt.
        root_ckptlogs: A string. Used for path to ckpts.
        subproject_name: A string. Used for path to ckpts.
        comment: A string. Used for path to ckpts.
        time_stamp: A string. Used for path to ckpts.
        path_resume: A string or None. The path to ckpt logs to be resumed. 
            path_resume is ignored if flag_resume=False.
        max_to_keep: An int. Set max_to_keep=0 or None to keep all the ckpts.
        config_path: A string. 
    Returns:
        ckpt: tf.train.Checkpoint object.
        ckpt_manager: tf.train.CheckpointManager object.
    Remark:
        Path to checkpoint files is 
            'root_ckptlogs'/'subproject_name'_'exp_phase'/'comment'_'time_stamp'/ckptXXX
    """
    # Naming rule
    dir_ckptlogs = "{}/{}_{}/{}_{}".format(
        root_ckptlogs, subproject_name, exp_phase, comment, time_stamp)

    if not os.path.exists(path_resume):
        os.makedirs(path_resume)

    if not(config_path is None):
        dir_configs = dir_ckptlogs + "/configs"

        if not os.path.exists(dir_configs):
            os.makedirs(dir_configs)

        now = datetime.datetime.now().strftime("%Y%m%d_%H%M%S%f")[:-3]        
        shutil.copyfile(config_path, dir_configs + "/config_{}.yaml".format(now))

    # Create ckpt
    #ckpt = tf.train.Checkpoint(step=global_step, optimizer=optimizer, net=model)
    ckpt = tf.train.Checkpoint(net=model)

    
    # If resume
    if flag_resume:
        assert os.path.exists(path_resume), "Not exist: path_ckpt {}".format(
            path_resume)

        # Create ckpt and manager for restore
        ckpt_manager_restore = tf.train.CheckpointManager(
            ckpt, path_resume, max_to_keep=max_to_keep)

        # Restore the latest ckpt log.
        ckpt.restore(ckpt_manager_restore.latest_checkpoint)
        print("Restored from {}".format(ckpt_manager_restore.latest_checkpoint))        
    
    # Create manager
    ckpt_manager = tf.train.CheckpointManager(
        ckpt, dir_ckptlogs, max_to_keep=max_to_keep)

    return ckpt, ckpt_manager


## User-defined parameters

In [2]:
gpu = 0 # which GPU to be used
batch_size = 50 
save_data = "train" # Run all the cells with "train" AND "test".

# NMNIST-H
path_resume = "./data-directory/trained_models/FE_NMNIST-H/" # Path to the feature extractor. Where ckpt files are contained.
tfr_train = './data-directory/nosaic_mnist-h_train.tfrecords' # input TFR
tfr_test = './data-directory/nosaic_mnist-h_test.tfrecords' # input TFR
tfr_feat_train = './data-directory/nosaic_mnist-h_feat_train.tfrecords' # output TFR name
tfr_feat_test = './data-directory/nosaic_mnist-h_feat_test.tfrecords' # output TFR name
duration = 20

# NMNIST-100f
# path_resume = "./data-directory/trained_models/FE_NMNIST-100f/" # where ckpt files are contained
# tfr_train = './data-directory/nosaic_mnist-100f-15pix_train.tfrecords' # input TFR
# tfr_test = './data-directory/nosaic_mnist-100f-15pix_test.tfrecords' # input TFR
# tfr_feat_train = './data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords' # output TFR name
# tfr_feat_test = './data-directory/nosaic_mnist-100f-15pix_feat_test.tfrecords' # output TFR name
# duration = 100


resnet_size = 110
resnet_version = 1
nb_cls = 10
final_size = 128
root_ckptlogs = "./data-directory"
subproject_name = "_"
exp_phase = "_"
comment = "_"

## Save TFRecords

In [3]:
set_gpu_devices(gpu)

In [4]:
# Read Nosaic MNIST
parsed_image_dataset_train, parsed_image_dataset_test = read_tfrecords_nosaic_mnist_tmp(
        record_file_train=tfr_train, 
        record_file_test=tfr_test, 
        batch_size=batch_size)

print(parsed_image_dataset_train)
print(parsed_image_dataset_test)

<BatchDataset shapes: {label: (None,), video: (None,)}, types: {label: tf.int64, video: tf.string}>
<BatchDataset shapes: {label: (None,), video: (None,)}, types: {label: tf.int64, video: tf.string}>


In [5]:
# Load model
dict_resparams = get_ressize_dependent_params(resnet_version, resnet_size)

model = ResNetModel(
    resnet_size=resnet_size,
    bottleneck=dict_resparams["bottleneck"],
    num_classes=nb_cls,
    kernel_size=dict_resparams["kernel_size"],
    conv_stride=dict_resparams["conv_stride"],
    first_pool_size=dict_resparams["first_pool_size"],
    first_pool_stride=dict_resparams["first_pool_stride"],
    block_sizes=dict_resparams["block_sizes"],
    block_strides=dict_resparams["block_strides"],
    final_size=final_size,
    resnet_version=resnet_version,
    data_format='channels_last',
    dtype=tf.float32
)

# Checkpoint
now = "0"
_, ckpt_manager = checkpoint_logger_tmp(
    model, 
    True, 
    root_ckptlogs, 
    subproject_name, 
    exp_phase,
    comment, 
    now, 
    path_resume)

Restored from ./data-directory/trained_models/FE_NMNIST-100f/ckpt_step20800_macrec0.43093-8


In [6]:
if save_data == "test":
    parsed_image_datasets = [parsed_image_dataset_test]
    record_files = [tfr_feat_test]
    list_numdata = [10000]
    
elif save_data == "train":
    parsed_image_datasets = [parsed_image_dataset_train]
    record_files = [tfr_feat_train]
    list_numdata = [60000]

else:
    raise ValueError
    
assert not os.path.exists(record_files[0]), "Remove or rename {}".format(record_files[0])

## save tfr

In [7]:
# Train or test
global_iter = 0
for parsed_image_dataset, record_file, num_data in zip(parsed_image_datasets, record_files, list_numdata):
    with tf.io.TFRecordWriter(record_file) as writer:##################### FOR SAFETY #################### 

        # Start loop
        for iter_b, feats in enumerate(parsed_image_dataset):
            # 1. Decode features, normalize images
            x_batch, y_batch = decode_nosaic_mnist(feats, duration=duration)
            iter_bs = y_batch.shape[0]
            labels_batch = np.int64(y_batch.numpy())
            
            x_batch, y_batch = reshape_for_featext(x_batch, y_batch, (28, 28, 1)) 
                # (bs*duration, 28,28,1), (bs*duration,)
            x_batch = normalize_images_nosaic_mnist(x_batch)

            
            # 2. Extract features
            _, losses, _, feats_batch = get_loss_fe(
            model, 
            x_batch, 
            y_batch, 
            training=False, 
            param_wd=None, 
            flag_wd=False,
            calc_grad=False
            )
            
            # Reshape (batch, duration, final size)
            feats_batch = tf.reshape(feats_batch, (iter_bs, duration, final_size))
            feats_batch = np.float32(feats_batch.numpy())
            
            # 3. Save images
            assert len(feats_batch) == len(labels_batch), "{}, {}".format(feats_batch.shape, labels_batch.shape)
            for feat, label in zip(feats_batch, labels_batch):
                np_to_tfr_fe(x=feat, y=label, writer=writer) 

            global_iter += 1

            # 4. Verbose
            if (iter_b+1) % 10 == 0:
                print("")
                print("Global Iter={:7d} Iter={:5d}/{:5d} xent={:7.5f}: writing {}"
                    .format(
                        global_iter,
                        iter_b + 1,
                        (num_data // batch_size) + 1 if num_data % batch_size != 0 else num_data // batch_size,
                        losses[1],
                        record_file))
                print(feat.shape)
                print(labels_batch)


Global Iter=     10 Iter=   10/ 1200 xent=1.49190: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[2 0 2 1 3 8 3 0 4 6 8 6 1 8 4 7 5 6 3 3 7 0 0 0 6 0 0 6 9 4 0 4 6 5 6 9 9
 6 7 4 0 2 8 1 4 0 3 0 2 4]

Global Iter=     20 Iter=   20/ 1200 xent=1.59342: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[0 8 8 0 6 8 5 2 7 7 5 7 8 8 2 6 8 5 4 5 2 5 8 3 5 7 6 1 8 8 7 1 0 7 6 3 8
 3 1 7 7 1 2 0 5 4 2 6 5 4]

Global Iter=     30 Iter=   30/ 1200 xent=1.54587: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[7 1 9 4 9 2 6 1 6 4 5 2 4 6 2 8 2 9 1 5 3 0 6 4 0 2 6 4 6 3 4 3 3 1 7 0 8
 0 7 0 3 1 5 6 6 3 7 6 4 4]

Global Iter=     40 Iter=   40/ 1200 xent=1.57113: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[3 0 1 0 4 3 9 8 6 5 2 0 7 7 3 3 6 8 6 3 8 1 2 5 2 3 9 1 2 0 3 8 6 2 7 5 5
 7 6 5 3 5 5 5 4 2 8 8 6 0]

Global Iter=     50 Iter=   50/ 1200 xent=1.47698: writ


Global Iter=    360 Iter=  360/ 1200 xent=1.60468: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[1 3 8 8 7 3 6 1 4 3 6 7 2 5 5 1 1 0 7 3 5 1 1 8 8 0 0 0 8 0 8 6 1 3 9 3 6
 2 5 9 6 6 8 4 9 7 4 2 6 1]

Global Iter=    370 Iter=  370/ 1200 xent=1.58907: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[6 1 5 8 7 9 1 6 7 2 3 5 3 9 7 6 9 1 8 4 0 7 1 7 1 1 9 0 3 6 6 9 8 0 0 5 2
 3 6 3 8 4 4 2 8 7 2 4 5 8]

Global Iter=    380 Iter=  380/ 1200 xent=1.64282: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[2 4 0 3 1 7 0 5 9 9 6 0 1 8 4 4 4 3 0 6 5 3 3 1 9 3 0 8 1 1 3 7 4 3 2 6 9
 1 9 0 8 5 5 5 0 4 8 4 1 3]

Global Iter=    390 Iter=  390/ 1200 xent=1.57331: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[2 0 0 1 1 9 7 9 0 7 8 3 7 0 9 3 1 1 5 8 7 8 1 4 5 0 6 3 8 0 8 8 7 8 0 7 4
 4 8 8 3 0 9 4 7 7 5 1 7 7]

Global Iter=    400 Iter=  400/ 1200 xent=1.63069: writ


Global Iter=    710 Iter=  710/ 1200 xent=1.47786: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[6 2 3 8 4 9 8 6 9 7 4 3 6 7 2 7 5 1 1 6 9 7 2 3 5 0 7 1 6 0 0 6 8 6 3 9 9
 2 7 9 6 8 2 1 5 8 3 8 0 1]

Global Iter=    720 Iter=  720/ 1200 xent=1.45684: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[6 0 1 5 7 3 8 0 7 0 1 3 9 2 0 9 6 0 9 2 1 5 1 3 6 2 3 3 5 2 7 9 1 8 4 5 4
 6 1 6 9 0 4 6 4 5 4 6 1 2]

Global Iter=    730 Iter=  730/ 1200 xent=1.44346: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[0 2 9 0 3 5 1 7 1 0 7 3 1 0 0 8 2 9 5 4 5 2 0 2 5 4 2 0 7 0 7 6 7 0 9 4 1
 3 3 4 6 4 7 9 7 2 2 6 8 4]

Global Iter=    740 Iter=  740/ 1200 xent=1.53370: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[4 4 0 0 7 5 8 8 7 2 1 2 8 6 1 2 6 7 6 2 7 3 2 7 0 6 0 9 7 7 7 6 0 8 0 6 6
 5 8 5 1 6 3 8 3 3 5 7 7 8]

Global Iter=    750 Iter=  750/ 1200 xent=1.61079: writ


Global Iter=   1060 Iter= 1060/ 1200 xent=1.54509: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[2 1 5 1 8 5 5 9 1 6 4 0 3 4 0 3 3 2 4 9 3 6 7 2 5 7 2 9 1 6 5 9 6 0 9 9 8
 0 4 0 0 2 9 1 2 8 8 3 3 6]

Global Iter=   1070 Iter= 1070/ 1200 xent=1.49866: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[3 1 2 9 2 3 1 8 3 2 7 9 2 6 4 7 4 8 7 8 2 7 8 6 3 9 6 3 0 3 1 4 8 7 9 5 2
 4 1 7 2 2 0 2 8 4 0 4 4 6]

Global Iter=   1080 Iter= 1080/ 1200 xent=1.58175: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[6 5 7 5 6 3 9 3 0 4 6 7 9 7 4 3 4 4 5 3 2 0 4 7 6 7 9 6 9 7 3 4 8 2 8 9 1
 1 7 9 0 4 3 7 3 2 2 1 2 9]

Global Iter=   1090 Iter= 1090/ 1200 xent=1.70812: writing ./data-directory/nosaic_mnist-100f-15pix_feat_train.tfrecords
(100, 128)
[2 4 3 4 4 9 0 2 4 6 5 5 7 2 8 3 6 8 9 8 8 1 2 2 8 4 1 3 1 0 0 2 5 4 2 7 8
 7 1 9 8 4 1 3 8 5 9 9 6 3]

Global Iter=   1100 Iter= 1100/ 1200 xent=1.52287: writ

# Read Feature TFR (Operation Confirmation)

In [8]:
# Read Feature TFR
feat_dim = final_size
bs_tmp = 1
dtype_feat = tf.float32
dtype_label = tf.int32
pid_tr, pid_val, pid_test = read_tfrecords_nosaic_mnist(
    tfr_feat_train, tfr_feat_test, bs_tmp)

if save_data == "test":
    show_pid = pid_test
elif save_data == "train":
    show_pid = pid_tr
else:
    raise ValueError

# Show
for i, features in enumerate(show_pid):
    vb, lb = decode_feat(features, duration, feat_dim, dtype_feat=tf.float32, dtype_label=tf.int32)
    if (i+1) % 5 == 0:
        #time.sleep(0.01)
        print("iter {}".format(i+1))
        print(vb)
        print(lb)

print("total num of data points: ", i+1)

iter 5
tf.Tensor(
[[[0.         0.         0.         ... 0.         0.         0.01543748]
  [0.         0.         0.         ... 0.5606132  0.         0.03800401]
  [0.         0.         0.         ... 0.3455401  0.         0.01401133]
  ...
  [0.         0.         0.         ... 0.02614271 0.0495941  0.05035767]
  [0.         0.         0.         ... 0.16977653 0.         0.13171521]
  [0.         0.         0.         ... 0.2997468  0.         0.08199634]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([1], shape=(1,), dtype=int32)
iter 10
tf.Tensor(
[[[0.         0.         0.         ... 0.2359258  0.06157814 0.0600617 ]
  [0.         0.10782    0.         ... 0.595366   0.         0.08194412]
  [0.         0.01772191 0.         ... 0.7355416  0.44150388 0.04792174]
  ...
  [0.         0.41683066 0.         ... 0.         0.0377505  0.        ]
  [0.         0.32337028 0.         ... 0.17482159 0.12724082 0.        ]
  [0.         0.2900678  0.         ... 0.         0.18817

iter 220
tf.Tensor(
[[[0.0000000e+00 3.4914158e-02 0.0000000e+00 ... 1.7541726e-01
   4.1360015e-01 5.1212657e-02]
  [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
   5.4877573e-01 0.0000000e+00]
  [0.0000000e+00 1.4041614e-02 0.0000000e+00 ... 0.0000000e+00
   0.0000000e+00 1.2707114e-01]
  ...
  [0.0000000e+00 9.2831925e-02 0.0000000e+00 ... 3.3253707e-02
   0.0000000e+00 1.7470606e-01]
  [0.0000000e+00 7.6767108e-03 0.0000000e+00 ... 0.0000000e+00
   0.0000000e+00 3.3100906e-01]
  [0.0000000e+00 0.0000000e+00 0.0000000e+00 ... 0.0000000e+00
   4.9606879e-04 2.9943230e-02]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([2], shape=(1,), dtype=int32)
iter 225
tf.Tensor(
[[[0.         0.47864473 0.         ... 0.13940434 0.02696365 0.06085723]
  [0.         0.00644996 0.         ... 0.12301994 0.01353329 0.0454511 ]
  [0.         0.09133085 0.         ... 0.00259181 0.         0.2265725 ]
  ...
  [0.         0.         0.         ... 0.10435585 0.         0.04769652]
  [

iter 435
tf.Tensor(
[[[0.         0.05389142 0.         ... 0.         0.18465786 0.06371967]
  [0.         0.         0.         ... 0.00276224 0.         0.09924559]
  [0.         0.         0.         ... 0.09422115 0.         0.22442234]
  ...
  [0.         0.         0.         ... 0.         0.         0.6852837 ]
  [0.         0.01459229 0.         ... 0.28248233 0.         0.17854354]
  [0.         0.03808917 0.         ... 0.04406107 0.14130455 0.21920693]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([8], shape=(1,), dtype=int32)
iter 440
tf.Tensor(
[[[0.         0.02654941 0.         ... 0.10736424 0.         0.0610646 ]
  [0.         0.17146583 0.         ... 0.06089282 0.         0.1436    ]
  [0.         0.         0.         ... 0.01870635 0.         0.04093348]
  ...
  [0.         0.02140736 0.         ... 0.35878664 0.         0.00227531]
  [0.         0.03253302 0.         ... 0.0063292  0.         0.04472752]
  [0.         0.         0.         ... 0.         0.02

iter 650
tf.Tensor(
[[[0.         0.4634425  0.         ... 0.02357076 0.         0.02540065]
  [0.         0.         0.         ... 0.38226303 0.17605326 0.10474396]
  [0.         0.3203157  0.00443704 ... 0.07080568 0.         0.07175744]
  ...
  [0.         0.23066354 0.         ... 0.12871565 0.03039993 0.01305363]
  [0.         0.         0.         ... 0.06911813 0.         0.03769416]
  [0.         0.6276857  0.         ... 0.         0.         0.00900244]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([2], shape=(1,), dtype=int32)
iter 655
tf.Tensor(
[[[0.         0.         0.         ... 0.         0.         0.25236565]
  [0.         0.         0.         ... 0.04528248 0.         0.01130639]
  [0.         0.00321482 0.         ... 0.         0.01863592 0.25394732]
  ...
  [0.         0.         0.         ... 0.3803839  0.         0.02444575]
  [0.         0.08545472 0.         ... 0.         0.01443702 0.0178843 ]
  [0.00161167 0.         0.         ... 0.02835896 0.02

iter 870
tf.Tensor(
[[[0.         0.00918951 0.         ... 0.         0.08236754 0.05798165]
  [0.         0.3351351  0.         ... 0.00165027 0.0114181  0.01119644]
  [0.         0.21989083 0.         ... 0.         0.00209885 0.16059716]
  ...
  [0.         0.22392063 0.         ... 0.03677113 0.01432643 0.5055548 ]
  [0.         0.3157494  0.         ... 0.         0.00480344 0.08845623]
  [0.         0.02564685 0.         ... 0.         0.         0.11976423]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([3], shape=(1,), dtype=int32)
iter 875
tf.Tensor(
[[[0.         0.02204244 0.         ... 0.0735973  0.01468189 0.03420523]
  [0.         0.         0.         ... 0.         0.         0.0765577 ]
  [0.         0.         0.         ... 0.01324979 0.00476452 0.09204337]
  ...
  [0.         0.         0.         ... 0.         0.04317947 0.06130181]
  [0.         0.00459043 0.         ... 0.11093852 0.         0.11740552]
  [0.         0.00376004 0.         ... 0.18414703 0.06

...

tf.Tensor([3], shape=(1,), dtype=int32)
iter 49040
tf.Tensor(
[[[0.         0.09620252 0.         ... 0.02494638 0.36663243 0.06799132]
  [0.         0.27767265 0.         ... 0.07814328 0.52767485 0.10672051]
  [0.         0.1454228  0.         ... 0.01252741 0.25324818 0.09854723]
  ...
  [0.         0.         0.         ... 0.15901294 0.34683657 0.06098121]
  [0.         0.         0.         ... 0.         0.27518693 0.07549407]
  [0.         0.39719242 0.         ... 0.         0.2338588  0.05078278]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([0], shape=(1,), dtype=int32)
iter 49045
tf.Tensor(
[[[0.         0.06961292 0.         ... 0.         0.02806278 0.07344153]
  [0.         0.         0.         ... 0.         0.         0.        ]
  [0.         0.         0.01661414 ... 0.02009122 0.         0.12013448]
  ...
  [0.         0.19297853 0.         ... 0.04669849 0.0408235  0.0282992 ]
  [0.         0.         0.         ... 0.11769345 0.01560763 0.05449285]
  [0.      

iter 49280
tf.Tensor(
[[[0.         0.         0.         ... 0.00475149 0.         0.02940651]
  [0.         0.         0.         ... 0.         0.01125205 0.18951237]
  [0.09470629 0.         0.         ... 0.6132268  0.00082242 0.        ]
  ...
  [0.         0.01263579 0.         ... 0.06925603 0.         0.07946287]
  [0.         0.00418137 0.         ... 0.03162404 0.         0.06469513]
  [0.         0.         0.         ... 0.06866906 0.         0.09221612]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([1], shape=(1,), dtype=int32)
iter 49285
tf.Tensor(
[[[0.         0.00746506 0.         ... 0.         0.         0.2184491 ]
  [0.         0.         0.         ... 0.         0.         0.23085147]
  [0.         0.         0.         ... 0.18235393 0.12953877 0.05857653]
  ...
  [0.01633384 0.02673937 0.         ... 0.         0.         0.27614224]
  [0.         0.13587648 0.         ... 0.         0.08100244 0.13895522]
  [0.         0.01819062 0.         ... 0.         

tf.Tensor([2], shape=(1,), dtype=int32)
iter 49525
tf.Tensor(
[[[0.         0.06396598 0.         ... 0.15675302 0.00034362 0.03796757]
  [0.         0.05019807 0.         ... 0.01653029 0.27846506 0.12386913]
  [0.         0.0102423  0.         ... 0.         0.         0.        ]
  ...
  [0.         0.23940101 0.         ... 0.01046642 0.         0.04628748]
  [0.         0.03354966 0.         ... 0.         0.03835652 0.1709137 ]
  [0.         0.         0.         ... 0.         0.         0.03999553]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([2], shape=(1,), dtype=int32)
iter 49530
tf.Tensor(
[[[0.         0.         0.         ... 0.03364293 0.06635065 0.02984662]
  [0.         0.03241247 0.         ... 0.         0.         0.2957199 ]
  [0.         0.19596194 0.         ... 0.         0.         0.04907656]
  ...
  [0.         0.11828702 0.         ... 0.3639492  0.11931771 0.00791247]
  [0.         0.08882039 0.         ... 0.03979863 0.         0.26856825]
  [0.      

iter 49765
tf.Tensor(
[[[0.         0.         0.         ... 0.0085849  0.         0.07141151]
  [0.         0.07866833 0.         ... 0.1301714  0.         0.02065456]
  [0.         0.08324595 0.         ... 0.0586739  0.         0.09303994]
  ...
  [0.         0.         0.         ... 0.12447746 0.         0.13837092]
  [0.         0.09152613 0.         ... 0.25520054 0.07990639 0.        ]
  [0.         0.01022337 0.         ... 0.         0.         0.11183005]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([3], shape=(1,), dtype=int32)
iter 49770
tf.Tensor(
[[[0.         0.08958037 0.         ... 0.01009063 0.13277888 0.00236465]
  [0.         0.01811326 0.         ... 0.14879538 0.07678504 0.01597423]
  [0.         0.00678645 0.         ... 0.3751509  0.0024437  0.13096923]
  ...
  [0.         0.         0.         ... 0.07283808 0.         0.15619113]
  [0.         0.34450006 0.         ... 0.         0.06594077 0.        ]
  [0.         0.01323598 0.         ... 0.         

iter 50000
tf.Tensor(
[[[0.         0.05509477 0.         ... 0.03269049 0.03838427 0.02956428]
  [0.         0.         0.         ... 0.         0.         0.07365881]
  [0.         0.5760032  0.         ... 0.11846454 0.0353203  0.12272008]
  ...
  [0.         0.57085884 0.         ... 0.         0.         0.25116158]
  [0.         0.36775586 0.         ... 0.         0.         0.318403  ]
  [0.         0.00542686 0.         ... 0.07156324 0.         0.14775743]]], shape=(1, 100, 128), dtype=float32)
tf.Tensor([3], shape=(1,), dtype=int32)
total num of data points:  50000
